# 1 - Data transformation

In [0]:
import pandas as pd
from pyspark.sql import Row, Column
from pyspark.sql.functions import *
from pyspark.sql.types import *

In [0]:
%fs ls

path name size modificationTime dbfs:/FileStore/ FileStore/ 0 0 dbfs:/databricks-datasets/ databricks-datasets/ 0 0 dbfs:/databricks-results/ databricks-results/ 0 0 dbfs:/local_disk0/ local_disk0/ 0 0

## File 1 - OI Results 1896-2016
ID - id of athlete
<br>
Name - name of athlete
<br>
Gender - gender of athlete
<br>
Age - age of athlete, can be NULL
<br>
Height - height of athlete, can be NULL
<br>
Weight - weight of athlete, can be NULL
<br>
Team - Country team the athlete represents
<br>
NOC - National Olympic Committee
<br>
Games - Summer or Winter season and year held
<br>
Year - when Olympics took place
<br>
Season - Summer or Winter
<br>
City - where Olympics took place
<br>
Sport - Athlete's sport
<br>
Event - Athlete's discipline
<br>
Medal - Medal athlete got on event
<br><br>
Link: https://www.kaggle.com/datasets/heesoo37/120-years-of-olympic-history-athletes-and-results

In [0]:
file_location = "dbfs:/FileStore/tables/athletes-1.csv"

#schema 
schema_def = StructType([StructField('ID', IntegerType(), True),
                     StructField('Name', StringType(), True),
                     StructField('Gender', StringType(), True),
                     StructField('Age', IntegerType(), True),
                     StructField('Height', IntegerType(), True),
                     StructField('Weight', IntegerType(), True),
                     StructField('Team', StringType(), True),
                     StructField('NOC', StringType(), True),
                     StructField('Games', StringType(), True),
                     StructField('Year', IntegerType(), True),
                     StructField('Season', StringType(), True),
                     StructField('City', StringType(), True),
                     StructField('Sport', StringType(), True),
                     StructField('Event', StringType(), True),
                     StructField('Medal', StringType(), True),
])

In [0]:
#load data from csv file
games = spark.read.csv(file_location, encoding="UTF-8", header=True, schema=schema_def) 
games.cache()

#replace null with -1 for age, height and weight
games = games.fillna(-1, 'Age')
games = games.withColumn('Medal', regexp_replace('Medal','NA', 'NO'))

#select columns
games_df = games.select(
    "ID",
    "Name",
    "Age",
    "NOC",
    "Games",
    "Sport",
    "Event",
    "Medal",
    "Team",
    "Gender"
)

games_df.cache()
# dropping ALL duplicate values
games_no_duplicates_df = games_df.drop_duplicates(subset=['Name','Games'])
# sorting by id and name
games_no_duplicates_df = games_no_duplicates_df.sort(['ID','Name'])

athl_df = games_no_duplicates_df.select("Age", "Medal").where((col("Medal") == "Gold") | (col("Medal") == "NO") & (col("Age") != -1))
# save in DBFS
athl_df.write.mode("overwrite").csv(path='dbfs:/FileStore/tables/athletes_results.csv', header=True)
athl_df.show()
display(games_no_duplicates_df)


games_no_duplicates = games_no_duplicates_df.rdd
games_list = games_no_duplicates.map(list).collect()

ID Name Age NOC Games Sport Event Medal Team Gender 1 A Dijiang 24 CHN 1992 Summer Basketball Basketball Men's Basketball NO China M 2 A Lamusi 23 CHN 2012 Summer Judo Judo Men's Extra-Lightweight NO China M 3 Gunnar Nielsen Aaby 24 DEN 1920 Summer Football Football Men's Football NO Denmark M 4 Edgar Lindenau Aabye 34 DEN 1900 Summer Tug-Of-War Tug-Of-War Men's Tug-Of-War Gold Denmark/Sweden M 5 Christine Jacoba Aaftink 21 NED 1988 Winter Speed Skating Speed Skating Women's 500 metres NO Netherlands F 5 Christine Jacoba Aaftink 27 NED 1994 Winter Speed Skating Speed Skating Women's 500 metres NO Netherlands F 5 Christine Jacoba Aaftink 25 NED 1992 Winter Speed Skating Speed Skating Women's 500 metres NO Netherlands F 6 Per Knut Aaland 33 USA 1994 Winter Cross Country Skiing Cross Country Skiing Men's 10 kilometres NO United States M 6 Per Knut Aaland 31 USA 1992 Winter Cross Country Skiing Cross Country Skiing Men's 10 kilometres NO United States M 7 John Aalberg 31 USA 1992 Winter Cross Country Skiing Cross Country Skiing Men's 10 kilometres NO United States M 7 John Aalberg 33 USA 1994 Winter Cross Country Skiing Cross Country Skiing Men's 10 kilometres NO United States M 8 Cornelia 'Cor' Aalten (-Strannood) 18 NED 1932 Summer Athletics Athletics Women's 100 metres NO Netherlands F 9 Antti Sami Aalto 26 FIN 2002 Winter Ice Hockey Ice Hockey Men's Ice Hockey NO Finland M 10 Einar Ferdinand 'Einari' Aalto 26 FIN 1952 Summer Swimming Swimming Men's 400 metres Freestyle NO Finland M 11 Jorma Ilmari Aalto 22 FIN 1980 Winter Cross Country Skiing Cross Country Skiing Men's 30 kilometres NO Finland M 12 Jyri Tapani Aalto 31 FIN 2000 Summer Badminton Badminton Men's Singles NO Finland M 13 Minna Maarit Aalto 34 FIN 2000 Summer Sailing Sailing Women's Windsurfer NO Finland F 13 Minna Maarit Aalto 30 FIN 1996 Summer Sailing Sailing Women's Windsurfer NO Finland F 14 Pirjo Hannele Aalto (Mattila-) 32 FIN 1994 Winter Biathlon Biathlon Women's 7.5 kilometres Sprint NO Finland F 15 Arvo Ossian Aaltonen 34 FIN 1924 Summer Swimming Swimming Men's 200 metres Breaststroke NO Finland M 15 Arvo Ossian Aaltonen 22 FIN 1912 Summer Swimming Swimming Men's 200 metres Breaststroke NO Finland M 15 Arvo Ossian Aaltonen 30 FIN 1920 Summer Swimming Swimming Men's 200 metres Breaststroke Bronze Finland M 16 Juhamatti Tapio Aaltonen 28 FIN 2014 Winter Ice Hockey Ice Hockey Men's Ice Hockey Bronze Finland M 17 Paavo Johannes Aaltonen 32 FIN 1952 Summer Gymnastics Gymnastics Men's Individual All-Around NO Finland M 17 Paavo Johannes Aaltonen 28 FIN 1948 Summer Gymnastics Gymnastics Men's Individual All-Around Bronze Finland M 18 Timo Antero Aaltonen 31 FIN 2000 Summer Athletics Athletics Men's Shot Put NO Finland M 19 Win Valdemar Aaltonen 54 FIN 1948 Summer Art Competitions Art Competitions Mixed Sculpturing, Unknown Event NO Finland M 20 Kjetil Andr Aamodt 20 NOR 1992 Winter Alpine Skiing Alpine Skiing Men's Downhill NO Norway M 20 Kjetil Andr Aamodt 34 NOR 2006 Winter Alpine Skiing Alpine Skiing Men's Downhill NO Norway M 20 Kjetil Andr Aamodt 30 NOR 2002 Winter Alpine Skiing Alpine Skiing Men's Downhill NO Norway M 20 Kjetil Andr Aamodt 26 NOR 1998 Winter Alpine Skiing Alpine Skiing Men's Downhill NO Norway M 20 Kjetil Andr Aamodt 22 NOR 1994 Winter Alpine Skiing Alpine Skiing Men's Downhill Silver Norway M 21 Ragnhild Margrethe Aamodt 27 NOR 2008 Summer Handball Handball Women's Handball Gold Norway F 22 Andreea Aanei 22 ROU 2016 Summer Weightlifting Weightlifting Women's Super-Heavyweight NO Romania F 23 Fritz Aanes 22 NOR 2000 Summer Wrestling Wrestling Men's Light-Heavyweight, Greco-Roman NO Norway M 23 Fritz Aanes 26 NOR 2004 Summer Wrestling Wrestling Men's Light-Heavyweight, Greco-Roman NO Norway M 24 Nils Egil Aaness 24 NOR 1960 Winter Speed Skating Speed Skating Men's 500 metres NO Norway M 24 Nils Egil Aaness 27 NOR 1964 Winter Speed Skating Speed Skating Men's 1,500 metres NO Norway M 25 Alf Lied Aanning 24 NOR 1920 Summer Gymnastics Gymnasti

### RDD map and reduce transformations

In [0]:
# athlete who participated in games
games_list_filter = [el for el in games_list if len(el[4]) > 0]
athletes_rdd = sc.parallelize(games_list)
athletes = athletes_rdd.map(lambda row: row[1]).cache()

athletes_count = athletes.map(lambda athlete: (athlete, 1)).reduceByKey(lambda c1,c2: c1+c2).sortBy(lambda gc: gc[1], ascending=False).cache()
athletes_map = athletes_count.take(5)

#Top 5 athletes who participated in most of the Olimpycs
for athlete in athletes_map:
    print(athlete)


('Ian Millar', 10)
('Hubert Raudaschl', 9)
('Afanasijs Kuzmins', 9)
('Paul Bert Elvstrm', 8)
('Aleksandr Vladimirovich Popov', 8)


In [0]:
# teams who had most participants in game
games_list_filter = [el for el in games_list if len(el[4]) > 0]
teams_rdd = sc.parallelize(games_list)
teams = teams_rdd.map(lambda row: row[3]+"_"+row[4]).cache()

teams_count = teams.map(lambda team: (team, 1)).reduceByKey(lambda c1,c2: c1+c2).sortBy(lambda tc: tc[1], ascending=False).cache()
teams_map = teams_count.take(5)

#Top 5 teams who had most participants in Olimpycs in one year
for team in teams_map:
    print(team)

('GBR_1908 Summer', 735)
('FRA_1900 Summer', 716)
('USA_1996 Summer', 648)
('AUS_2000 Summer', 617)
('USA_2008 Summer', 588)


In [0]:
teams_rdd = sc.parallelize(games_list)
teams = teams_rdd.map(lambda row: row[3]+"_"+row[4]).cache()

teams_count = teams.map(lambda team: (team, 1)).reduceByKey(lambda c1,c2: c1+c2).sortBy(lambda tc: tc[1], ascending=False).cache()
teams_map = teams_count.take(5)

#Top 5 teams who had most participants in Olimpycs in one year
for team in teams_map:
    print(team)

('GBR_1908 Summer', 735)
('FRA_1900 Summer', 716)
('USA_1996 Summer', 648)
('AUS_2000 Summer', 617)
('USA_2008 Summer', 588)


In [0]:
def delete_team_duplicates(list):
    list_filter = []
    for elem in list:
        new_elem = elem[3]+"_"+elem[4]+"_"+elem[6]
        if (elem[8] == 'Team') and new_elem not in list_filter:
            list.remove(elem)

    return list

In [0]:
#country with most won medals in games
games_list_filter = games_df.drop_duplicates(subset=['NOC', 'Games', 'Event', 'Medal']).collect()

#filter medals only
games_list_filter = [el for el in games_list_filter if el[7] != 'NO']

medals_rdd = sc.parallelize(games_list_filter)

medals = medals_rdd.map(lambda row: row[3]+"_"+row[4]).cache()

medals_count = medals.map(lambda medal: (medal, 1)).reduceByKey(lambda c1,c2: c1+c2).sortBy(lambda mc: mc[1], ascending=False).cache()
medals_map = medals_count.take(5)

#Top 5 teams who had most medals in Olimpycs in one year
for team in medals_map:
    print(team)
    

('USA_1904 Summer', 230)
('URS_1980 Summer', 195)
('USA_1984 Summer', 173)
('GBR_1908 Summer', 143)
('URS_1988 Summer', 131)


In [0]:
games_no_duplicates_athlete = games_df.drop_duplicates(subset=['Name','Games','Event'])
games_no_duplicates_athlete = games_no_duplicates_athlete.rdd
games_list_athlete = games_no_duplicates_athlete.map(list).collect()
games_list_filter = [el for el in games_list_athlete if el[7] != 'NO']

athletes_medals_rdd = sc.parallelize(games_list_filter)

athletes_medals = athletes_medals_rdd.map(lambda row: row[1]).cache()

athletes_medals_count = athletes_medals.map(lambda athlete: (athlete, 1)).reduceByKey(lambda c1,c2: c1+c2).sortBy(lambda amc: amc[1], ascending=False).cache()
athletes_medals_map = athletes_medals_count.take(5)

for athlete in athletes_medals_map:
    print(athlete)

('Michael Fred Phelps. II', 28)
('Larysa Semenivna Latynina (Diriy-)', 18)
('Nikolay Yefimovich Andrianov', 15)
('Borys Anfiyanovych Shakhlin', 13)
('Ole Einar Bjrndalen', 13)


### Transformation for OI data 1986-2016
We want to get number of gold, silver and bronze medals for each Game and each NOC who won medals on OI Games each year

In [0]:
games_df_new = games_df.drop_duplicates(subset=['NOC', 'Games', 'Event', 'Medal'])

# GOLD MEDALS FOR NOC AND GAME
gold_df = games_df_new.select("*").where((col("Medal") == "Gold")).groupBy(["NOC", "Games"]).agg(count("*").alias("Gold"))
# SILVER MEDALS FOR NOC AND GAME
silver_df = games_df_new.select("*").where(col("Medal") == "Silver").groupBy(["NOC", "Games"]).agg(count("*").alias("Silver"))
#rename columns
silver_df = silver_df.withColumnRenamed("NOC","NOC 1").withColumnRenamed("Games","Games 1")

# BRONZE MEDALS FOR NOC AND GAME
bronze_df = games_df_new.select("*").where(col("Medal") == "Bronze").groupBy(["NOC", "Games"]).agg(count("*").alias("Bronze"))
#rename columns
bronze_df = bronze_df.withColumnRenamed("NOC","NOC 2").withColumnRenamed("Games","Games 2")

# JOIN ALL TABLES 
first_join = gold_df.join(silver_df, (gold_df["NOC"] == silver_df["NOC 1"]) & (gold_df["Games"] == silver_df["Games 1"]), "outer")
first_join = first_join.withColumn('NOC',when(col('NOC').isNotNull(),col('NOC')).otherwise(col('NOC 1')))
first_join = first_join.withColumn('Games',when(col('Games').isNotNull(),col('Games')).otherwise(col('Games 1')))

second_join = first_join.join(bronze_df, (first_join["NOC"] == bronze_df["NOC 2"]) & (first_join["Games"] == bronze_df["Games 2"]), "outer")
second_join = second_join.withColumn('NOC',when(col('NOC').isNotNull(),col('NOC')).otherwise(col('NOC 2')))
second_join = second_join.withColumn('Games',when(col('Games').isNotNull(),col('Games')).otherwise(col('Games 2')))

# Remove columns
final_df = second_join.drop("NOC 1", "NOC 2", "Games 1", "Games 2")

final_df = final_df.fillna(0, ['Gold', 'Silver', 'Bronze'])

# Total
final_df = final_df.withColumn("Total",  expr("Gold + Silver + Bronze"))
# Sort
final_df = final_df.sort(desc("Total"))
#final_df = final_df.sort(asc("Games"), asc("NOC"))

display(final_df)

NOC Games Gold Silver Bronze Total USA 1904 Summer 76 79 75 230 URS 1980 Summer 80 69 46 195 USA 1984 Summer 82 61 30 173 GBR 1908 Summer 56 50 37 143 URS 1988 Summer 54 31 46 131 GDR 1980 Summer 47 37 42 126 URS 1976 Summer 49 41 35 125 USA 2016 Summer 46 37 38 121 EUN 1992 Summer 45 38 29 112 USA 1932 Summer 44 36 30 110 USA 2008 Summer 36 39 35 110 USA 1992 Summer 37 34 37 108 USA 1968 Summer 45 28 34 107 URS 1960 Summer 43 29 31 103 USA 2012 Summer 46 28 29 103 FRA 1900 Summer 28 40 34 102 GDR 1988 Summer 37 35 30 102 GER 1936 Summer 38 31 32 101 USA 1996 Summer 44 32 25 101 USA 2004 Summer 36 39 26 101 CHN 2008 Summer 51 21 28 100 URS 1972 Summer 50 27 22 99 USA 1924 Summer 45 27 27 99 URS 1956 Summer 37 29 32 98 USA 1920 Summer 41 27 27 95 USA 1972 Summer 33 31 30 94 USA 1976 Summer 34 35 25 94 USA 1988 Summer 36 31 27 94 URS 1964 Summer 30 30 33 93 URS 1968 Summer 29 32 30 91 USA 2000 Summer 36 24 31 91 GDR 1976 Summer 40 25 25 90 RUS 2004 Summer 28 26 36 90 USA 1964 Summer 36 26 28 90 RUS 2000 Summer 32 28 29 89 CHN 2012 Summer 38 27 23 88 USA 1948 Summer 38 27 19 84 GER 1992 Summer 33 21 28 82 RUS 2012 Summer 24 26 32 82 USA 1952 Summer 40 19 17 76 USA 1956 Summer 32 25 17 74 RUS 2008 Summer 23 21 28 72 USA 1960 Summer 34 21 16 71 CHN 2016 Summer 26 18 26 70 URS 1952 Summer 22 29 19 70 GBR 2016 Summer 27 23 17 67 GDR 1972 Summer 20 23 23 66 GBR 2012 Summer 29 17 19 65 GER 1996 Summer 20 18 27 65 SWE 1912 Summer 24 24 17 65 SWE 1920 Summer 19 20 25 64 CHN 2004 Summer 32 17 14 63 RUS 1996 Summer 26 21 16 63 USA 1912 Summer 26 18 19 63 FRG 1984 Summer 17 19 23 59 AUS 2000 Summer 16 25 17 58 CHN 2000 Summer 28 16 14 58 USA 1936 Summer 24 21 12 57 GER 2000 Summer 13 17 26 56 RUS 2016 Summer 19 17 20 56 USA 1928 Summer 22 18 16 56 USA 1900 Summer 21 16 17 54 CHN 1992 Summer 16 22 15 53 ROU 1984 Summer 19 16 17 52 AUS 2004 Summer 17 16 17 50 CHN 1996 Summer 16 22 12 50 GER 1964 Summer 10 22 18 50 GER 2004 Summer 13 16 20 49 GBR 2008 Summer 19 13 16 48 AUS 2008 Summer 14 15 17 46 SWE 1948 Summer 17 11 18 46 USA 1908 Summer 22 12 12 46 CAN 1984 Summer 10 18 16 44 GER 2012 Summer 11 19 14 44 GRE 1896 Summer 10 17 17 44 GBR 1920 Summer 14 16 13 43 BEL 1920 Summer 16 12 14 42 FRA 1920 Summer 9 20 13 42 FRA 2016 Summer 10 18 14 42 GBR 1900 Summer 19 11 12 42 GER 1960 Summer 12 19 11 42 GER 2016 Summer 17 10 15 42 HUN 1952 Summer 16 10 16 42 AUS 1996 Summer 9 9 23 41 BUL 1980 Summer 8 16 17 41 FRA 1906 Summer 15 10 16 41 FRA 2008 Summer 7 16 18 41 GBR 1912 Summer 10 15 16 41 GER 2008 Summer 16 10 15 41 JPN 2016 Summer 12 8 21 41 FRA 1924 Summer 14 14 12 40 FRG 1972 Summer 13 11 16 40 FRG 1988 Summer 11 14 15 40 FRG 1976 Summer 10 12 17 39 GER 1928 Summer 11 9 19 39 FRA 2000 Summer 13 14 11 38 JPN 2012 Summer 7 14 17 38 FIN 1924 Summer 14 13 10 37 FRA 1996 Summer 15 7 15 37 GBR 1984 Summer 5 11 21 37 JPN 2004 Summer 16 9 12 37 USA 2010 Winter 9 15 13 37 GER 2002 Winter 12 16 8 36 ITA 1932 Summer 12 12 12 36 ITA 1960 Summer 13 10 13 36 AUS 1956 Summer 13 8 14 35 AUS 2012 Summer 7 16 12 35 BUL 1988 Summer 10 12 13 35 FRA 2012 Summer 11 11 13 35 GBR 1924 Summer 9 14 12 35 GRE 1906 Summer 8 14 13 35 HUN 1972 Summer 6 13 16 35 ITA 1996 Summer 13 10 12 35 SWE 1952 Summer 12 13 10 35 FIN 1920 Summer 15 10 9 34 ITA 2000 Summer 13 8 13 34 USA 2002 Winter 10 13 11 34 FRA 2004 Summer 11 9 13 33 KOR 1988 Summer 12 10 11 33 RUS 2014 Winter 13 11 9 33 CHN 1984 Summer 15 8 9 32 FRA 1948 Summer 11 6 15 32 HUN 1968 Summer 10 10 12 32 HUN 1980 Summer 7 10 15 32 ITA 1984 Summer 14 6 12 32 ITA 2004 Summer 10 11 11 32 POL 1980 Summer 3 14 15 32 CUB 1992 Summer 14 6 11 31 ITA 1948 Summer 9 12 10 31 JPN 1984 Summer 10 7 14 31 KOR 2008 Summer 13 10 8 31 GBR 2004 Summer 9 9 12 30 GER 2010 Winter 10 13 7 30 HUN 1992 Summer 11 12 7 30 KOR 2004 Summer 9 12 9 30 AUS 2016 Summer 8 11 10 29 CUB 2000 Summer 11 11 7 29 FRA 1992 Summer 8 5 16 29 GER 1998 Winter 12 9 8 29 GER 2006 Winter 11 12 6 29 JPN 1964 Summer 16 5 8 29 JPN 1972 Summer 13 8 8 29 NOR 1920 Summer 1

In [0]:
gm = games.filter(col("Games").contains("Summer"))
gm = gm.select("Event").distinct().orderBy("Event")
display(gm)

Event Aeronautics Mixed Aeronautics Alpinism Mixed Alpinism Archery Men's Au Chapelet, 33 metres Archery Men's Au Chapelet, 50 metres Archery Men's Au Cordon Dore, 33 metres Archery Men's Au Cordon Dore, 50 metres Archery Men's Championnat Du Monde Archery Men's Continental Style Archery Men's Double American Round Archery Men's Double York Round Archery Men's Individual Archery Men's Pole Archery, Large Birds, Individual Archery Men's Pole Archery, Large Birds, Team Archery Men's Pole Archery, Small Birds, Individual Archery Men's Pole Archery, Small Birds, Team Archery Men's Sur La Perche a La Herse Archery Men's Sur La Perche a La Pyramide Archery Men's Target Archery, 28 metres, Individual Archery Men's Target Archery, 28 metres, Team Archery Men's Target Archery, 33 metres, Individual Archery Men's Target Archery, 33 metres, Team Archery Men's Target Archery, 50 metres, Individual Archery Men's Target Archery, 50 metres, Team Archery Men's Team Archery Men's Team Round Archery Men's Unknown Event Archery Women's Double Columbia Round Archery Women's Double National Round Archery Women's Individual Archery Women's Team Archery Women's Team Round Art Competitions Mixed Architecture Art Competitions Mixed Architecture, Architectural Designs Art Competitions Mixed Architecture, Designs For Town Planning Art Competitions Mixed Architecture, Unknown Event Art Competitions Mixed Literature Art Competitions Mixed Literature, Dramatic Works Art Competitions Mixed Literature, Epic Works Art Competitions Mixed Literature, Lyric Works Art Competitions Mixed Literature, Unknown Event Art Competitions Mixed Music Art Competitions Mixed Music, Compositions For Orchestra Art Competitions Mixed Music, Compositions For Solo Or Chorus Art Competitions Mixed Music, Instrumental And Chamber Art Competitions Mixed Music, Unknown Event Art Competitions Mixed Music, Vocals Art Competitions Mixed Painting Art Competitions Mixed Painting, Applied Arts Art Competitions Mixed Painting, Drawings And Water Colors Art Competitions Mixed Painting, Graphic Arts Art Competitions Mixed Painting, Paintings Art Competitions Mixed Painting, Unknown Event Art Competitions Mixed Sculpturing Art Competitions Mixed Sculpturing, Medals Art Competitions Mixed Sculpturing, Medals And Plaques Art Competitions Mixed Sculpturing, Medals And Reliefs Art Competitions Mixed Sculpturing, Reliefs Art Competitions Mixed Sculpturing, Statues Art Competitions Mixed Sculpturing, Unknown Event Art Competitions Mixed Unknown Event Athletics Men's 1,500 metres Athletics Men's 1,500 metres Walk Athletics Men's 1,600 metres Medley Relay Athletics Men's 10 kilometres Walk Athletics Men's 10 mile Walk Athletics Men's 10,000 metres Athletics Men's 100 metres Athletics Men's 110 metres Hurdles Athletics Men's 2,500 metres Steeplechase Athletics Men's 2,590 metres Steeplechase Athletics Men's 20 kilometres Walk Athletics Men's 200 metres Athletics Men's 200 metres Hurdles Athletics Men's 3 mile, Team Athletics Men's 3,000 metres Steeplechase Athletics Men's 3,000 metres Walk Athletics Men's 3,000 metres, Team Athletics Men's 3,200 metres Steeplechase Athletics Men's 3,500 metres Walk Athletics Men's 4 mile, Team Athletics Men's 4 x 100 metres Relay Athletics Men's 4 x 400 metres Relay Athletics Men's 4,000 metres Steeplechase Athletics Men's 400 metres Athletics Men's 400 metres Hurdles Athletics Men's 5 mile Athletics Men's 5,000 metres Athletics Men's 5,000 metres, Team Athletics Men's 50 kilometres Walk Athletics Men's 56-pound Weight Throw Athletics Men's 60 metres Athletics Men's 800 metres Athletics Men's All-Around Championship Athletics Men's Cross-Country, Individual Athletics Men's Cross-Country, Team Athletics Men's Decathlon Athletics Men's Discus Throw Athletics Men's Discus Throw, Both Hands Athletics Men's Discus Throw, Greek Style Athletics Men's Hammer Throw Athletics Men's High Jump Athletics Men's Javelin Throw Athletics Men's Javelin Throw, Both Hands Athletics Men's 

## File 2 - OI Results 2020
ID - id of athlete
<br>
Team - Olympic team name
<br>
Gold - number of team gold medals 
<br>
Silver - number of team silver medals 
<br>
Bronze - number of team bronze medals 
<br>
Total - sum of number of team medals 
<br>
Rank - overall team placement
<br><br>
Link: https://www.kaggle.com/datasets/berkayalan/2021-olympics-medals-in-tokyo

In [0]:
# File 2 -> Results from 2020 Olympics
file_location_2 = "dbfs:/FileStore/tables/oi_summer_2020-2.csv"

#schema 
schema_def_2 = StructType([StructField('ID', IntegerType(), True),
                     StructField('Team', StringType(), True),
                     StructField('Gold', IntegerType(), True),
                     StructField('Silver', IntegerType(), True),
                     StructField('Bronze', IntegerType(), True),
                     StructField('Total', IntegerType(), True),
                     StructField('Rank', IntegerType(), True),
])

### Transformation for OI data 2020
We want to make column NOC by joining with existing dataframe we made with transforming oi data 1986-2016

In [0]:
oi_2020 = spark.read.csv(file_location_2, encoding="UTF-8", header=True, schema=schema_def_2)
display(oi_2020)

# Add column NOC
oi_2020 = oi_2020.withColumn("Games 2", lit("2020 Summer"))
oi_2020 = oi_2020.join(games_df, (oi_2020["Team"] == games_df["Team"]), "outer").cache()
oi_2020 = oi_2020.select("NOC", "Games 2", "Gold", "Silver", "Bronze", "Total").where(col("Games 2") == "2020 Summer").drop_duplicates(subset=["NOC", "Games 2"])
oi_2020 = oi_2020.fillna('RUS', 'NOC')
display(oi_2020)

ID Team Gold Silver Bronze Total Rank 1 United States 39 41 33 113 1 2 China 38 32 18 88 2 3 Japan 27 14 17 58 5 4 Great Britain 22 21 22 65 4 5 ROC 20 28 23 71 3 6 Australia 17 7 22 46 6 7 Netherlands 10 12 14 36 9 8 France 10 12 11 33 10 9 Germany 10 11 16 37 8 10 Italy 10 10 20 40 7 11 Canada 7 6 11 24 11 12 Brazil 7 6 8 21 12 13 New Zealand 7 6 7 20 13 14 Cuba 7 3 5 15 18 15 Hungary 6 7 7 20 13 16 Republic of Korea 6 4 10 20 13 17 Poland 4 5 5 14 19 18 Czech Republic 4 4 3 11 23 19 Kenya 4 4 2 10 25 20 Norway 4 2 2 8 29 21 Jamaica 4 1 4 9 26 22 Spain 3 8 6 17 17 23 Sweden 3 6 0 9 26 24 Switzerland 3 4 6 13 20 25 Denmark 3 4 4 11 23 26 Croatia 3 3 2 8 29 27 Islamic Republic of Iran 3 2 2 7 33 28 Serbia 3 1 5 9 26 29 Belgium 3 1 3 7 33 30 Bulgaria 3 1 2 6 39 31 Slovenia 3 1 1 5 42 32 Uzbekistan 3 0 2 5 42 33 Georgia 2 5 1 8 29 34 Chinese Taipei 2 4 6 12 22 35 Turkey 2 2 9 13 20 36 Greece 2 1 1 4 47 36 Uganda 2 1 1 4 47 38 Ecuador 2 1 0 3 60 39 Ireland 2 0 2 4 47 39 Israel 2 0 2 4 47 41 Qatar 2 0 1 3 60 42 Bahamas 2 0 0 2 66 42 Kosovo 2 0 0 2 66 44 Ukraine 1 6 12 19 16 45 Belarus 1 3 3 7 33 46 Romania 1 3 0 4 47 46 Venezuela 1 3 0 4 47 48 India 1 2 4 7 33 49 Hong Kong, China 1 2 3 6 39 50 Philippines 1 2 1 4 47 50 Slovakia 1 2 1 4 47 52 South Africa 1 2 0 3 60 53 Austria 1 1 5 7 33 54 Egypt 1 1 4 6 39 55 Indonesia 1 1 3 5 42 56 Ethiopia 1 1 2 4 47 56 Portugal 1 1 2 4 47 58 Tunisia 1 1 0 2 66 59 Estonia 1 0 1 2 66 59 Fiji 1 0 1 2 66 59 Latvia 1 0 1 2 66 59 Thailand 1 0 1 2 66 63 Bermuda 1 0 0 1 77 63 Morocco 1 0 0 1 77 63 Puerto Rico 1 0 0 1 77 66 Colombia 0 4 1 5 42 67 Azerbaijan 0 3 4 7 33 68 Dominican Republic 0 3 2 5 42 69 Armenia 0 2 2 4 47 70 Kyrgyzstan 0 2 1 3 60 71 Mongolia 0 1 3 4 47 72 Argentina 0 1 2 3 60 72 San Marino 0 1 2 3 60 74 Jordan 0 1 1 2 66 74 Malaysia 0 1 1 2 66 74 Nigeria 0 1 1 2 66 77 Bahrain 0 1 0 1 77 77 Saudi Arabia 0 1 0 1 77 77 Lithuania 0 1 0 1 77 77 North Macedonia 0 1 0 1 77 77 Namibia 0 1 0 1 77 77 Turkmenistan 0 1 0 1 77 83 Kazakhstan 0 0 8 8 29 84 Mexico 0 0 4 4 47 85 Finland 0 0 2 2 66 86 Botswana 0 0 1 1 77 86 Burkina Faso 0 0 1 1 77 86 C�te d'Ivoire 0 0 1 1 77 86 Ghana 0 0 1 1 77 86 Grenada 0 0 1 1 77 86 Kuwait 0 0 1 1 77 86 Republic of Moldova 0 0 1 1 77 86 Syrian Arab Republic 0 0 1 1 77

NOC Games 2 Gold Silver Bronze Total RUS 2020 Summer 3 2 2 7 TPE 2020 Summer 2 4 6 12 SWE 2020 Summer 3 6 0 9 PHI 2020 Summer 1 2 1 4 MAS 2020 Summer 0 1 1 2 FIJ 2020 Summer 1 0 1 2 TUR 2020 Summer 2 2 9 13 GER 2020 Summer 10 11 16 37 JOR 2020 Summer 0 1 1 2 FRA 2020 Summer 10 12 11 33 GRE 2020 Summer 2 1 1 4 KOS 2020 Summer 2 0 0 2 SVK 2020 Summer 1 2 1 4 ARG 2020 Summer 0 1 2 3 BEL 2020 Summer 3 1 3 7 GBR 2020 Summer 22 21 22 65 SMR 2020 Summer 0 1 2 3 QAT 2020 Summer 2 0 1 3 ECU 2020 Summer 2 1 0 3 FIN 2020 Summer 0 0 2 2 GHA 2020 Summer 0 0 1 1 BAH 2020 Summer 2 0 0 2 IND 2020 Summer 1 2 4 7 USA 2020 Summer 39 41 33 113 CHN 2020 Summer 38 32 18 88 BLR 2020 Summer 1 3 3 7 KUW 2020 Summer 0 0 1 1 PUR 2020 Summer 1 0 0 1 CRO 2020 Summer 3 3 2 8 NGR 2020 Summer 0 1 1 2 ITA 2020 Summer 10 10 20 40 LTU 2020 Summer 0 1 0 1 TKM 2020 Summer 0 1 0 1 NOR 2020 Summer 4 2 2 8 ESP 2020 Summer 3 8 6 17 CUB 2020 Summer 7 3 5 15 DEN 2020 Summer 3 4 4 11 IRL 2020 Summer 2 0 2 4 THA 2020 Summer 1 0 1 2 MAR 2020 Summer 1 0 0 1 VEN 2020 Summer 1 3 0 4 UKR 2020 Summer 1 6 12 19 ISR 2020 Summer 2 0 2 4 MEX 2020 Summer 0 0 4 4 EST 2020 Summer 1 0 1 2 GEO 2020 Summer 2 5 1 8 INA 2020 Summer 1 1 3 5 MGL 2020 Summer 0 1 3 4 AZE 2020 Summer 0 3 4 7 GRN 2020 Summer 0 0 1 1 ARM 2020 Summer 0 2 2 4 TUN 2020 Summer 1 1 0 2 KSA 2020 Summer 0 1 0 1 UGA 2020 Summer 2 1 1 4 NAM 2020 Summer 0 1 0 1 SUI 2020 Summer 3 4 6 13 ETH 2020 Summer 1 1 2 4 JAM 2020 Summer 4 1 4 9 LAT 2020 Summer 1 0 1 2 CAN 2020 Summer 7 6 11 24 UZB 2020 Summer 3 0 2 5 KGZ 2020 Summer 0 2 1 3 CZE 2020 Summer 4 4 3 11 BRA 2020 Summer 7 6 8 21 KEN 2020 Summer 4 4 2 10 SLO 2020 Summer 3 1 1 5 DOM 2020 Summer 0 3 2 5 JPN 2020 Summer 27 14 17 58 BOT 2020 Summer 0 0 1 1 NZL 2020 Summer 7 6 7 20 POL 2020 Summer 4 5 5 14 POR 2020 Summer 1 1 2 4 AUS 2020 Summer 17 7 22 46 ROU 2020 Summer 1 3 0 4 BUL 2020 Summer 3 1 2 6 AUT 2020 Summer 1 1 5 7 EGY 2020 Summer 1 1 4 6 KAZ 2020 Summer 0 0 8 8 SRB 2020 Summer 3 1 5 9 BUR 2020 Summer 0 0 1 1 RSA 2020 Summer 1 2 0 3 BER 2020 Summer 1 0 0 1 BRN 2020 Summer 0 1 0 1 COL 2020 Summer 0 4 1 5 HUN 2020 Summer 6 7 7 20 NED 2020 Summer 10 12 14 36

Union dataframe we got with transforming oi data 1986-2016 and results from oi 2020 and adding dense ranking for NOC for each OI Games

In [0]:
# Add Olympics results from 2020 to all
final_result = final_df.union(oi_2020).cache()
final_result = final_result.sort(desc("Total"))

display(final_result)

NOC Games Gold Silver Bronze Total USA 1904 Summer 76 79 75 230 URS 1980 Summer 80 69 46 195 USA 1984 Summer 82 61 30 173 GBR 1908 Summer 56 50 37 143 URS 1988 Summer 54 31 46 131 GDR 1980 Summer 47 37 42 126 URS 1976 Summer 49 41 35 125 USA 2016 Summer 46 37 38 121 USA 2020 Summer 39 41 33 113 EUN 1992 Summer 45 38 29 112 USA 2008 Summer 36 39 35 110 USA 1932 Summer 44 36 30 110 USA 1992 Summer 37 34 37 108 USA 1968 Summer 45 28 34 107 URS 1960 Summer 43 29 31 103 USA 2012 Summer 46 28 29 103 GDR 1988 Summer 37 35 30 102 FRA 1900 Summer 28 40 34 102 USA 1996 Summer 44 32 25 101 GER 1936 Summer 38 31 32 101 USA 2004 Summer 36 39 26 101 CHN 2008 Summer 51 21 28 100 URS 1972 Summer 50 27 22 99 USA 1924 Summer 45 27 27 99 URS 1956 Summer 37 29 32 98 USA 1920 Summer 41 27 27 95 USA 1988 Summer 36 31 27 94 USA 1976 Summer 34 35 25 94 USA 1972 Summer 33 31 30 94 URS 1964 Summer 30 30 33 93 USA 2000 Summer 36 24 31 91 URS 1968 Summer 29 32 30 91 USA 1964 Summer 36 26 28 90 RUS 2004 Summer 28 26 36 90 GDR 1976 Summer 40 25 25 90 RUS 2000 Summer 32 28 29 89 CHN 2020 Summer 38 32 18 88 CHN 2012 Summer 38 27 23 88 USA 1948 Summer 38 27 19 84 GER 1992 Summer 33 21 28 82 RUS 2012 Summer 24 26 32 82 USA 1952 Summer 40 19 17 76 USA 1956 Summer 32 25 17 74 RUS 2008 Summer 23 21 28 72 USA 1960 Summer 34 21 16 71 CHN 2016 Summer 26 18 26 70 URS 1952 Summer 22 29 19 70 GBR 2016 Summer 27 23 17 67 GDR 1972 Summer 20 23 23 66 GBR 2020 Summer 22 21 22 65 SWE 1912 Summer 24 24 17 65 GBR 2012 Summer 29 17 19 65 GER 1996 Summer 20 18 27 65 SWE 1920 Summer 19 20 25 64 USA 1912 Summer 26 18 19 63 RUS 1996 Summer 26 21 16 63 CHN 2004 Summer 32 17 14 63 FRG 1984 Summer 17 19 23 59 JPN 2020 Summer 27 14 17 58 AUS 2000 Summer 16 25 17 58 CHN 2000 Summer 28 16 14 58 USA 1936 Summer 24 21 12 57 USA 1928 Summer 22 18 16 56 RUS 2016 Summer 19 17 20 56 GER 2000 Summer 13 17 26 56 USA 1900 Summer 21 16 17 54 CHN 1992 Summer 16 22 15 53 ROU 1984 Summer 19 16 17 52 AUS 2004 Summer 17 16 17 50 GER 1964 Summer 10 22 18 50 CHN 1996 Summer 16 22 12 50 GER 2004 Summer 13 16 20 49 GBR 2008 Summer 19 13 16 48 AUS 2020 Summer 17 7 22 46 SWE 1948 Summer 17 11 18 46 AUS 2008 Summer 14 15 17 46 USA 1908 Summer 22 12 12 46 CAN 1984 Summer 10 18 16 44 GER 2012 Summer 11 19 14 44 GRE 1896 Summer 10 17 17 44 GBR 1920 Summer 14 16 13 43 HUN 1952 Summer 16 10 16 42 GBR 1900 Summer 19 11 12 42 GER 1960 Summer 12 19 11 42 FRA 1920 Summer 9 20 13 42 BEL 1920 Summer 16 12 14 42 GER 2016 Summer 17 10 15 42 FRA 2016 Summer 10 18 14 42 GBR 1912 Summer 10 15 16 41 JPN 2016 Summer 12 8 21 41 FRA 2008 Summer 7 16 18 41 GER 2008 Summer 16 10 15 41 FRA 1906 Summer 15 10 16 41 BUL 1980 Summer 8 16 17 41 AUS 1996 Summer 9 9 23 41 ITA 2020 Summer 10 10 20 40 FRG 1972 Summer 13 11 16 40 FRA 1924 Summer 14 14 12 40 FRG 1988 Summer 11 14 15 40 FRG 1976 Summer 10 12 17 39 GER 1928 Summer 11 9 19 39 FRA 2000 Summer 13 14 11 38 JPN 2012 Summer 7 14 17 38 GER 2020 Summer 10 11 16 37 FRA 1996 Summer 15 7 15 37 USA 2010 Winter 9 15 13 37 GBR 1984 Summer 5 11 21 37 JPN 2004 Summer 16 9 12 37 FIN 1924 Summer 14 13 10 37 NED 2020 Summer 10 12 14 36 ITA 1932 Summer 12 12 12 36 ITA 1960 Summer 13 10 13 36 GER 2002 Winter 12 16 8 36 SWE 1952 Summer 12 13 10 35 ITA 1996 Summer 13 10 12 35 HUN 1972 Summer 6 13 16 35 GBR 1924 Summer 9 14 12 35 AUS 1956 Summer 13 8 14 35 FRA 2012 Summer 11 11 13 35 GRE 1906 Summer 8 14 13 35 BUL 1988 Summer 10 12 13 35 AUS 2012 Summer 7 16 12 35 USA 2002 Winter 10 13 11 34 FIN 1920 Summer 15 10 9 34 ITA 2000 Summer 13 8 13 34 FRA 2020 Summer 10 12 11 33 RUS 2014 Winter 13 11 9 33 KOR 1988 Summer 12 10 11 33 FRA 2004 Summer 11 9 13 33 FRA 1948 Summer 11 6 15 32 CHN 1984 Summer 15 8 9 32 HUN 1980 Summer 7 10 15 32 POL 1980 Summer 3 14 15 32 ITA 1984 Summer 14 6 12 32 ITA 2004 Summer 10 11 11 32 HUN 1968 Summer 10 10 12 32 CUB 1992 Summer 14 6 11 31 ITA 1948 Summer 9 12 10 31 JPN 1984 Summer 10 7 14 31 KOR 2008 Summer 13 10 8 31 HUN 1992 Summer 11 12 7 30 KOR 2004 Summer 9 12 9 30 GER

In [0]:
from pyspark.sql.window import Window

windowSpec = Window.partitionBy(final_result["Games"]).orderBy(desc("Total"))
final_result = final_result.withColumn("Rank", dense_rank().over(windowSpec))
display(final_result)

NOC Games Gold Silver Bronze Total Rank GRE 1896 Summer 10 17 17 44 1 USA 1896 Summer 11 6 2 19 2 GER 1896 Summer 7 5 2 14 3 FRA 1896 Summer 5 4 2 11 4 GBR 1896 Summer 3 3 3 9 5 HUN 1896 Summer 2 1 3 6 6 DEN 1896 Summer 1 2 3 6 6 AUT 1896 Summer 2 1 2 5 7 AUS 1896 Summer 2 0 1 3 8 SUI 1896 Summer 1 2 0 3 8 FRA 1900 Summer 28 40 34 102 1 USA 1900 Summer 21 16 17 54 2 GBR 1900 Summer 19 11 12 42 3 BEL 1900 Summer 6 7 5 18 4 SUI 1900 Summer 6 2 1 9 5 GER 1900 Summer 4 3 1 8 6 NED 1900 Summer 1 2 4 7 7 DEN 1900 Summer 2 3 2 7 7 AUS 1900 Summer 3 0 3 6 8 AUT 1900 Summer 0 3 3 6 8 ITA 1900 Summer 3 2 0 5 9 NOR 1900 Summer 0 2 3 5 9 HUN 1900 Summer 1 2 2 5 9 BOH 1900 Summer 0 1 2 3 10 CAN 1900 Summer 1 0 1 2 11 CUB 1900 Summer 1 1 0 2 11 IND 1900 Summer 0 2 0 2 11 SWE 1900 Summer 1 0 1 2 11 HAI 1900 Summer 1 0 0 1 12 NZL 1900 Summer 1 0 0 1 12 ESP 1900 Summer 1 0 0 1 12 MEX 1900 Summer 0 0 1 1 12 COL 1900 Summer 0 1 0 1 12 LUX 1900 Summer 1 0 0 1 12 USA 1904 Summer 76 79 75 230 1 GER 1904 Summer 4 5 7 16 2 CAN 1904 Summer 4 1 1 6 3 AUT 1904 Summer 2 1 1 4 4 AUS 1904 Summer 0 3 1 4 4 HUN 1904 Summer 2 1 1 4 4 CUB 1904 Summer 4 0 0 4 4 SUI 1904 Summer 1 0 2 3 5 FRA 1904 Summer 0 2 0 2 6 GRE 1904 Summer 1 0 1 2 6 GBR 1904 Summer 1 1 0 2 6 NOR 1904 Summer 2 0 0 2 6 FRA 1906 Summer 15 10 16 41 1 GRE 1906 Summer 8 14 13 35 2 GBR 1906 Summer 8 12 5 25 3 USA 1906 Summer 12 5 6 23 4 ITA 1906 Summer 7 6 3 16 5 GER 1906 Summer 4 6 4 14 6 SWE 1906 Summer 2 5 7 14 6 HUN 1906 Summer 2 5 3 10 7 AUT 1906 Summer 3 3 3 9 8 SUI 1906 Summer 4 3 1 8 9 BEL 1906 Summer 2 2 3 7 10 DEN 1906 Summer 3 2 1 6 11 FIN 1906 Summer 2 1 1 4 12 NED 1906 Summer 0 1 2 3 13 AUS 1906 Summer 0 0 3 3 13 BOH 1906 Summer 0 0 2 2 14 CAN 1906 Summer 1 1 0 2 14 NOR 1906 Summer 1 1 0 2 14 GBR 1908 Summer 56 50 37 143 1 USA 1908 Summer 22 12 12 46 2 SWE 1908 Summer 8 6 11 25 3 FRA 1908 Summer 5 5 9 19 4 CAN 1908 Summer 3 3 10 16 5 GER 1908 Summer 3 5 5 13 6 HUN 1908 Summer 3 4 2 9 7 NOR 1908 Summer 2 3 3 8 8 BEL 1908 Summer 1 5 2 8 8 FIN 1908 Summer 1 1 3 5 9 ANZ 1908 Summer 1 2 2 5 9 DEN 1908 Summer 0 2 3 5 9 GRE 1908 Summer 0 3 1 4 10 ITA 1908 Summer 2 2 0 4 10 RUS 1908 Summer 1 2 0 3 11 NED 1908 Summer 0 0 2 2 12 RSA 1908 Summer 1 1 0 2 12 BOH 1908 Summer 0 0 2 2 12 AUT 1908 Summer 0 0 1 1 13 SWE 1912 Summer 24 24 17 65 1 USA 1912 Summer 26 18 19 63 2 GBR 1912 Summer 10 15 16 41 3 GER 1912 Summer 6 13 7 26 4 FIN 1912 Summer 9 8 9 26 4 FRA 1912 Summer 7 5 3 15 5 DEN 1912 Summer 1 6 5 12 6 NOR 1912 Summer 4 1 5 10 7 CAN 1912 Summer 3 2 3 8 8 HUN 1912 Summer 3 2 3 8 8 ITA 1912 Summer 5 1 2 8 8 ANZ 1912 Summer 2 2 3 7 9 RSA 1912 Summer 4 2 0 6 10 BEL 1912 Summer 2 1 3 6 10 RUS 1912 Summer 0 2 3 5 11 AUT 1912 Summer 0 2 2 4 12 NED 1912 Summer 0 0 3 3 13 GRE 1912 Summer 1 0 1 2 14 SUI 1912 Summer 1 0 0 1 15 USA 1920 Summer 41 27 27 95 1 SWE 1920 Summer 19 20 25 64 2 GBR 1920 Summer 14 16 13 43 3 FRA 1920 Summer 9 20 13 42 4 BEL 1920 Summer 16 12 14 42 4 FIN 1920 Summer 15 10 9 34 5 NOR 1920 Summer 10 10 9 29 6 ITA 1920 Summer 14 6 5 25 7 DEN 1920 Summer 3 9 1 13 8 SUI 1920 Summer 2 2 7 11 9 NED 1920 Summer 4 2 5 11 9 RSA 1920 Summer 3 4 3 10 10 CAN 1920 Summer 3 3 3 9 11 BRA 1920 Summer 1 1 1 3 12 EST 1920 Summer 1 2 0 3 12 AUS 1920 Summer 0 2 1 3 12 JPN 1920 Summer 0 2 0 2 13 ESP 1920 Summer 0 2 0 2 13 TCH 1920 Summer 0 0 2 2 13 LUX 1920 Summer 0 1 0 1 14 NZL 1920 Summer 0 0 1 1 14 GRE 1920 Summer 0 1 0 1 14 USA 1924 Summer 45 27 27 99 1 FRA 1924 Summer 14 14 12 40 2 FIN 1924 Summer 14 13 10 37 3 GBR 1924 Summer 9 14 12 35 4 SWE 1924 Summer 4 13 12 29 5 SUI 1924 Summer 7 8 10 25 6 ITA 1924 Summer 8 3 5 16 7 BEL 1924 Summer 3 7 3 13 8 DEN 1924 Summer 2 6 3 11 9 NED 1924 Summer 4 1 6 11 9 HUN 1924 Summer 2 4 4 10 10 NOR 1924 Summer 5 2 3 10 10 TCH 1924 Summer 1 4 5 10 10 EST 1924 Summer 1 1 4 6 11 ARG 1924 Summer 1 3 2 6 11 AUS 1924 Summer 3 1 2 6 11 AUT 1924 Summer 0 3 1 4 12 CAN 1924 Summer 0 3 1 4 12 RSA 1924 Summer 1 1 1 3 13 LUX 1924 Summer 1 1 0 2 14 IRL 1924 Summer 0 1 1 2 14 P

#### Saving transformed data in DBFS for later analysis

In [0]:
final_result.write.mode("overwrite").csv(path='dbfs:/FileStore/tables/oi_results-2.csv', header=True)

## File 3 - RENT
Date - when advertisment was posted
<br>
Price - anual price for house
<br>
Bedrooms - number of bedrooms
<br>
Bathrooms - nummber of bathrooms
<br>
Sqft living - living area in square foot
<br>
Sqft LOT - square footage or area 
<br>
Floors - number of floors
<br>
Waterfront - if house has waterfront or not
<br>
View - number of house views
<br>
Condition - number of conditions
<br>
Sqft above - all living square feet in a home that is above the ground
<br>
Sqft basement - living square feet in a home that is bellothe ground
<br>
Year built - when house is built
<br>
Year renovated - when house is renovated, or 0 if not
<br>
Street - in which street house is located
<br>
City - where house is located
<br><br>
Link: https://www.kaggle.com/datasets/shree1992/housedata

In [0]:
# File 3 -> House renting
file_location_3 = "dbfs:/FileStore/tables/data.csv"

#schema 
schema_def_3 = StructType([StructField('Date', DateType(), True),
                     StructField('Price', DoubleType(), True),
                     StructField('Bedrooms', DoubleType(), True),
                     StructField('Bathrooms', DoubleType(), True),
                     StructField('Sqft Living', IntegerType(), True),
                     StructField('Sqft LOT', IntegerType(), True),
                     StructField('Floors', DoubleType(), True),
                     StructField('Waterfront', IntegerType(), True),
                     StructField('View', IntegerType(), True),
                     StructField('Condition', IntegerType(), True),
                     StructField('Sqft above', IntegerType(), True),
                     StructField('Sqft basement', DoubleType(), True),
                     StructField('Year built', IntegerType(), True),
                     StructField('Year renovated', IntegerType(), True),
                     StructField('Street', StringType(), True),
                     StructField('City', StringType(), True),
])

Transformation for RENT data
We want to make column Old depending on year when house was built

In [0]:
rent_df = spark.read.csv(file_location_3, encoding="UTF-8", header=True, schema=schema_def_3).cache()
rent_df = rent_df.select("Price", "Bedrooms", "Bathrooms", "Sqft Living", "Floors", "Year built").where(col("Price") > 0).cache()
rent_df = rent_df.withColumn("Old", when(((col("Year built") >= 1900) & (col("Year built") <= 1950)), lit("20th c - first half")).when((col("Year built") >= 1951) & (col("Year built") <= 2000), lit("20th c - second half")).when(col("Year built") > 2000, lit("21th")))

steps = rent_df.select("Bedrooms").distinct().collect()
for step in steps[:]:
    print(step[0])
          #step[0])
#    _df = rent_df.select("*").where(col("Bedrooms") == step[0])
#    _df.coalesce(1).write.mode("append").option("header", "true").csv('dbfs:/FileStore/stream')

8.0
0.0
7.0
1.0
4.0
3.0
2.0
6.0
5.0
9.0


In [0]:
# save in DBFS
rent_df.write.mode("overwrite").csv(path='dbfs:/FileStore/tables/rent_results-2.csv', header=True)

In [0]:
rent_df.groupBy("Old").agg(avg("Price"), count("*")).show()

+--------------------+-----------------+--------+
|                 Old|       avg(Price)|count(1)|
+--------------------+-----------------+--------+
| 20th c - first half|565139.0624241706|    1124|
|20th c - second half|536592.2376613059|    2473|
|                21th|604634.0011274718|     954|
+--------------------+-----------------+--------+



## File 4 - Diet
<br>
Gender - male or female
<br>
Diet - type of diet
<br>
Weigth - weight before diet
<br>
Weigth After - number of bathrooms
<br><br>
Link: https://www.kaggle.com/datasets/zaranadoshi/anova-diet

In [0]:
# File 4 -> Diet plan
file_location_4 = "dbfs:/FileStore/tables/Diet.csv"

#schema 
schema_def_4 = StructType([StructField('Gender', StringType(), True),
                     StructField('Diet', StringType(), True),
                     StructField('Weight', DoubleType(), True),
                     StructField('Weight After', DoubleType(), True),
])

Transformation for Diet data
We want to make column Difference that is made in weight after six weeks diet

In [0]:
diet_df = spark.read.csv(file_location_4, encoding="UTF-8", header=True, schema=schema_def_4)
diet_df = diet_df.withColumn("Difference", round(diet_df["Weight"]-diet_df["Weight After"], 2)).cache()
display(diet_df)
# save in DBFS
diet_df.write.mode("overwrite").csv(path='dbfs:/FileStore/tables/diet_results.csv', header=True)

Gender Diet Weight Weight After Difference M B 60.0 60.0 0.0 M B 103.0 103.0 0.0 F A 58.0 54.2 3.8 F A 60.0 54.0 6.0 F A 64.0 63.3 0.7 F A 64.0 61.1 2.9 F A 65.0 62.2 2.8 F A 66.0 64.0 2.0 F A 67.0 65.0 2.0 F A 69.0 60.5 8.5 F A 70.0 68.1 1.9 F A 70.0 66.9 3.1 F A 72.0 70.5 1.5 F A 72.0 69.0 3.0 F A 72.0 68.4 3.6 F A 82.0 81.1 0.9 F B 58.0 60.1 -2.1 F B 58.0 56.0 2.0 F B 59.0 57.3 1.7 F B 61.0 56.7 4.3 F B 62.0 55.0 7.0 F B 63.0 62.4 0.6 F B 63.0 60.3 2.7 F B 63.0 59.4 3.6 F B 65.0 62.0 3.0 F B 66.0 64.0 2.0 F B 68.0 63.8 4.2 F B 68.0 63.3 4.7 F B 76.0 72.7 3.3 F B 77.0 77.5 -0.5 F C 60.0 53.0 7.0 F C 62.0 56.4 5.6 F C 64.0 60.6 3.4 F C 65.0 58.2 6.8 F C 66.0 58.2 7.8 F C 67.0 61.6 5.4 F C 67.0 60.2 6.8 F C 69.0 61.8 7.2 F C 70.0 63.0 7.0 F C 70.0 62.7 7.3 F C 72.0 71.1 0.9 F C 72.0 64.4 7.6 F C 73.0 68.9 4.1 F C 75.0 68.7 6.3 F C 76.0 71.0 5.0 M A 71.0 71.6 -0.6 M A 72.0 70.9 1.1 M A 74.0 69.5 4.5 M A 78.0 73.9 4.1 M A 80.0 71.0 9.0 M A 80.0 77.6 2.4 M A 83.0 79.1 3.9 M A 85.0 81.5 3.5 M A 87.0 81.9 5.1 M A 88.0 84.5 3.5 M B 71.0 66.8 4.2 M B 75.0 72.6 2.4 M B 75.0 69.2 5.8 M B 76.0 72.5 3.5 M B 78.0 72.7 5.3 M B 78.0 76.3 1.7 M B 79.0 73.6 5.4 M B 79.0 72.9 6.1 M B 79.0 71.1 7.9 M B 80.0 81.4 -1.4 M B 80.0 75.7 4.3 M C 71.0 68.5 2.5 M C 73.0 72.1 0.9 M C 76.0 72.5 3.5 M C 78.0 77.5 0.5 M C 78.0 75.2 2.8 M C 78.0 69.4 8.6 M C 79.0 74.5 4.5 M C 83.0 80.2 2.8 M C 84.0 79.9 4.1 M C 85.0 79.7 5.3 M C 87.0 77.8 9.2 M C 88.0 81.9 6.1